In [1]:
import yaml
import json
import re

In [2]:
def change_serverless_config_file_with_memory(memoryList):
    with open("./../hyperflow-awslambda-executor/serverless.yml") as f:
            serverless_config = yaml.load(f)
    serverless_config['functions'] = {}
    function_executors = serverless_config['functions']
    for memory in memoryList:
        executor_name = 'aws-executor-' + str(memory)
        function_spec = {}
        function_spec['handler'] = 'handler.executor'
        function_spec['description'] = 'AWS executor ' + str(memory) + 'MB memory size'
        function_spec['memorySize'] = memory
        events_to_add = []
        http_event = {}
        http_event_elements = {}
        http_event_elements['path'] = executor_name
        http_event_elements['method'] = 'post'
        http_event['http'] = http_event_elements
        events_to_add.append(http_event)
        function_spec['events'] = events_to_add
        
        function_executors[executor_name] = function_spec


    with open("./../hyperflow-awslambda-executor/serverless.yml", "w") as f:
            yaml.dump(serverless_config, f)

In [3]:

lambda_possible_ram = list(range(128, 3072 ,64))

#change_serverless_config_file_with_memory(lambda_possible_ram)

#! cd ./../hyperflow-awslambda-executor && sls deploy


In [2]:
%%capture cap
! cd ./../hyperflow-awslambda-executor && sls deploy

In [6]:
lambda_core_url_matcher = re.search('POST - (.+?)aws-executor', cap.stdout)
lambda_core_url = lambda_core_url_matcher.group(1)
js_config_string = '\n\nexports.resources = {\n'
for memory in lambda_possible_ram:
    js_config_string+= '  "' + str(memory) + '": "' + lambda_core_url + 'aws-executor-' + str(memory) +'",\n'
js_config_string += '};\n'

# with open("./awsLambdaCommand.config.js", "a") as myfile:
#     myfile.write(js_config_string)

In [3]:
cap.stdout

'Serverless: \x1bDeprecation warning: Support for "package.include" and "package.exclude" will be removed with next major release. Please use "package.patterns" instead\x1b\r\n            \x1bMore Info: https://www.serverless.com/framework/docs/deprecations/#NEW_PACKAGE_PATTERNS\x1b\r\nServerless: \x1bDeprecation warning: Starting with version 3.0.0, following property will be replaced:\x1b\r\n\x1b              "provider.iamRoleStatements" -> "provider.iam.role.statements"\x1b\r\n            \x1bMore Info: https://www.serverless.com/framework/docs/deprecations/#PROVIDER_IAM_SETTINGS\x1b\r\nServerless: \x1bDeprecation warning: Resolution of lambda version hashes was improved with better algorithm, which will be used in next major release.\x1b\r\n\x1b            Switch to it now by setting "provider.lambdaHashingVersion" to "20201221"\x1b\r\n            \x1bMore Info: https://www.serverless.com/framework/docs/deprecations/#LAMBDA_HASHING_VERSION_V2\x1b\r\nServerless: \x1bPackaging servic

In [23]:
with open('./generated-dag.json') as result_json:
    data = json.load(result_json)

In [24]:
new_tasks = []
for task in data['tasks']:
    if task['name'] == 'mProject':
        task['config']['deploymentType'] = str(1984) 
    new_tasks.append(task)

In [25]:
data['tasks']  = new_tasks

In [26]:
data

{'tasks': [{'name': 'mProject',
   'function': 'awsLambdaCommand',
   'type': 'dataflow',
   'firingLimit': 1,
   'config': {'executor': {'executable': 'mProject',
     'args': ['-X',
      '2mass-atlas-980914s-k0830221.fits',
      'p2mass-atlas-980914s-k0830221.fits',
      'region-oversized.hdr']},
    'id': 659,
    'deploymentType': '1984',
    'scheduledStartTime': 750,
    'scheduledFinishTime': 14792},
   'ins': [1006, 1],
   'outs': [1007, 1008],
   'startTime': {'128': 750,
    '192': 750,
    '256': 750,
    '320': 750,
    '384': 750,
    '448': 750,
    '512': 750,
    '576': 750,
    '640': 750,
    '704': 750,
    '768': 750,
    '832': 750,
    '896': 750,
    '960': 750,
    '1024': 750,
    '1088': 750,
    '1152': 750,
    '1216': 750,
    '1280': 750,
    '1344': 750,
    '1408': 750,
    '1472': 750,
    '1536': 750,
    '1600': 750,
    '1664': 750,
    '1728': 750,
    '1792': 750,
    '1856': 750,
    '1920': 750,
    '1984': 750,
    '2048': 750,
    '2112': 75

In [27]:
with open('./generated-dag.json', 'w+') as result_json:
    json.dump(data, result_json, indent=4)